In [140]:
%load_ext autoreload
%autoreload 2
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:90% !important; }</style>"))

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [145]:
import pandas as pd
pd.set_option('display.max_colwidth', -1)

import numpy as np
import sklearn
from sklearn import metrics
import nltk 
from collections import Counter
import matplotlib.pyplot as plt
import itertools
import ast

nltk.download('stopwords')
from nltk.corpus import stopwords 
stop_words = set(stopwords.words('english'))


### BOOTLEG ###
import sys
sys.path.append('/dfs/scratch1/simran/bootleg_downstream/pipeline_scripts')
import load_entity_profiles

[nltk_data] Downloading package stopwords to
[nltk_data]     /lfs/1/simran/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [150]:
from load_entity_profiles import es, esp, type_vocab, typeid2typename, type_vocab_wd, typeid2typename_wd, alias_qid_count, rel_to_name

In [195]:
# Bootleg utility functions:
# BY ALIAS: 
def get_candidates(alias):
    try:
        # To get qid candidates of an alias
        cands = esp.get_qid_cands(alias)
        return cands
#         print(f"Cands {cands}")
#         print([es.get_title(qid) for qid in cands])
    except:
        cands = esp.get_qid_cands(alias)
    
get_candidates('distortion')

['Q899871',
 'Q2914540',
 'Q1347355',
 'Q186634',
 'Q639',
 'Q17001864',
 'Q5168467',
 'Q5283070',
 'Q53672378',
 'Q3710452',
 'Q5283068',
 'Q30598895',
 'Q2520974']

In [222]:
# Manual User Inputs
model = '/dfs/scratch1/simran/bootleg_downstream/error_outputs/09082020-113324_bootleg_dev_rev_ent.csv' #baseline spanbert without bootleg
spanbert = '/dfs/scratch1/simran/bootleg_downstream/error_outputs/0916_tacred_bert_dev_predictions.csv'
# model = '/dfs/scratch1/simran/bootleg_downstream/error_outputs/09082020-113218_bootleg_test_rev_ent.csv' #baseline spanbert without bootleg
# spanbert = '/dfs/scratch1/simran/bootleg_downstream/error_outputs/0916_tacred_bert_test_predictions.csv'

In [223]:
LABEL_TO_ID = {'no_relation': 0, 'per:title': 1, 'org:top_members/employees': 2, 'per:employee_of': 3, 
               'org:alternate_names': 4, 'org:country_of_headquarters': 5, 'per:countries_of_residence': 6, 
               'org:city_of_headquarters': 7, 'per:cities_of_residence': 8, 'per:age': 9, 
               'per:stateorprovinces_of_residence': 10, 'per:origin': 11, 'org:subsidiaries': 12, 
               'org:parents': 13, 'per:spouse': 14, 'org:stateorprovince_of_headquarters': 15, 'per:children': 16, 
               'per:other_family': 17, 'per:alternate_names': 18, 'org:members': 19, 'per:siblings': 20, 
               'per:schools_attended': 21, 'per:parents': 22, 'per:date_of_death': 23, 'org:member_of': 24, 
               'org:founded_by': 25, 'org:website': 26, 'per:cause_of_death': 27, 
               'org:political/religious_affiliation': 28, 'org:founded': 29, 'per:city_of_death': 30, 
               'org:shareholders': 31, 'org:number_of_employees/members': 32, 'per:date_of_birth': 33, 
               'per:city_of_birth': 34, 'per:charges': 35, 'per:stateorprovince_of_death': 36, 'per:religion': 37, 
               'per:stateorprovince_of_birth': 38, 'per:country_of_birth': 39, 'org:dissolved': 40, 
               'per:country_of_death': 41}

LABEL_LST = list(LABEL_TO_ID.keys())

STANFORD_NER_TYPES = ['DATE', 'LOCATION', 'MONEY', 'ORGANIZATION', 'PERCENT', 'PERSON', 'TIME']
punctuation = [',', ':', '.', ';', "'", ')', '(', "'s", '--', '-', '``', "''"]

In [224]:
# Load the model data 
df_results = pd.read_csv(model)
df_results.rename(columns={'prediction':'prediction_model'}, inplace=True)

# Load the baseline data
df_results_spanbert = pd.read_csv(spanbert)
map_id_pred = {}
for ind, row in df_results_spanbert.iterrows():
    map_id_pred[row['id']] = row['prediction']
df_results['prediction_spanbert'] = df_results['id'].map(map_id_pred)


for key in df_results.columns.values:
    if key != 'prediction':
        df_results_spanbert[key] = df_results[key]

# error rates
df_errors = df_results[df_results['relation'] != df_results['prediction_model']]
df_errors_spanbert = df_results[df_results['relation'] != df_results['prediction_spanbert']]

print("FULL_model size: ", df_results.shape)
print("ERRS_model size: ", df_errors.shape)

print("FULL_spanbert size: ", df_results_spanbert.shape)
print("ERRS_spanbert size: ", df_errors_spanbert.shape)



FULL_model size:  (22631, 27)
ERRS_model size:  (2596, 27)
FULL_spanbert size:  (22631, 28)
ERRS_spanbert size:  (1944, 27)


In [225]:
sub_df = df_results_spanbert[df_results_spanbert['relation'] == df_results_spanbert['prediction_spanbert']]
for ind, row in sub_df.iterrows():
    print(row)
    print()
    if ind == 20:
        break

id                     e7798fb926b9403cfcd2                                                                                                                                                                                                                                                                                                                                            
prediction             per:title                                                                                                                                                                                                                                                                                                                                                       
obj                    ['chairman']                                                                                                                                                                                                                     

In [226]:
# Utility functions: accepts a df with corrected slices, and outputs the predicted result
from sklearn.metrics import f1_score
from sklearn.metrics import precision_recall_fscore_support as score
def score_corrections(df):
    import scorer
    scorer.score(df['relation_model'].tolist(), df['prediction_model'].tolist(), verbose=True)
    df_errs = df[df['relation_model'] != df['prediction_model']]
    print("Number of Errors: ", df_errs.shape[0])
# score_corrections(df_results)

In [227]:
# basic error rate by relation 
def error_rate_by_relation(df_r, key, df_e):
    relation_df = pd.DataFrame(columns=['relation','error_rate','error_count','total_count'])
    index = 0
    for k, v in LABEL_TO_ID.items():
        df_relation_tot = df_r[df_r[key] == k] # all rows with k = true trelation
        tot = df_relation_tot.shape[0] # number of examples with this true relation
    
        df_relation_err = df_e[df_e[key] == k] # error rows with k = true trelation
        err = df_relation_err.shape[0] # number of errors with this true relation
        error_rate = err/tot
    
        relation_df.loc[index] = pd.Series({'relation':k, 'error_rate':error_rate, 'error_count':err, 'total_count':tot})
        index += 1
    
    print(relation_df.sort_values('relation'))

## Analysis by Relation

In [228]:
#error_rate_by_relation(df_results, 'relation_model', df_errors)
relation_df = pd.DataFrame(columns=['relation','errrate_span','errcount_span', 'errrate_boot','errcount_boot','total_count'])
index = 0
for k, v in LABEL_TO_ID.items():
        df_relation_tot_span = df_results_spanbert[df_results_spanbert['relation'] == k] # all rows with k = true trelation
        tot_span = df_relation_tot_span.shape[0] # number of examples with this true relation
        if tot_span > 0:
    
            df_relation_err_span = df_errors_spanbert[df_errors_spanbert['relation'] == k] # error rows with k = true trelation
            err_span = df_relation_err_span.shape[0] # number of errors with this true relation
            error_rate_span = err_span/tot_span

            df_relation_tot_boot = df_results[df_results['relation'] == k] # all rows with k = true trelation
            tot_boot = df_relation_tot_boot.shape[0] # number of examples with this true relation

            df_relation_err_boot = df_errors[df_errors['relation'] == k] # error rows with k = true trelation
            err_boot = df_relation_err_boot.shape[0] # number of errors with this true relation
            error_rate_boot = err_boot/tot_boot

            relation_df.loc[index] = pd.Series({'relation':k, 'errrate_span':error_rate_span, 'errcount_span':err_span, 'errrate_boot':error_rate_boot,'errcount_boot': err_boot, 'total_count':tot_span})
            index += 1
    
print(relation_df.sort_values('relation'))

                               relation  errrate_span errcount_span  \
0   no_relation                          0.046795      811            
4   org:alternate_names                  0.097701      34             
7   org:city_of_headquarters             0.268519      29             
5   org:country_of_headquarters          0.415385      81             
40  org:dissolved                        1.000000      1              
29  org:founded                          0.117647      4              
25  org:founded_by                       0.160000      12             
24  org:member_of                        1.000000      7              
19  org:members                          0.109375      7              
32  org:number_of_employees/members      0.291667      7              
13  org:parents                          0.543210      44             
28  org:political/religious_affiliation  0.285714      4              
31  org:shareholders                     0.828571      29             
15  or

### What relations are commonly mistaken for each other? 
This shows relations where model starts to do better than the baseline (green), and worse than the baseline (red). Next questions: which of these relations match up to relations contained in Bootleg? Look at examples to see why these get confused for one another. 

- A lot of the inversions are between <no relation, X>, or <X, no relation>

In [159]:
cm_model = sklearn.metrics.confusion_matrix(df_errors['relation'], df_errors['prediction_model'], labels=LABEL_LST, sample_weight=None, normalize=None)
cm_spanbert = sklearn.metrics.confusion_matrix(df_errors_spanbert['relation'], df_errors_spanbert['prediction_spanbert'], labels=LABEL_LST, sample_weight=None, normalize=None)

thresh = 1
print("These are the relations that most commonly get mistaken for one another (barring confusions with no_relaiton)")
print("TRUE: ", ", PRED: ", ", MODEL numerr: ", ", SPANBERT numerr: ")
confusions = {}
for i, j in itertools.product(range(cm_model.shape[0]), range(cm_model.shape[1])):
    if LABEL_LST[i] not in confusions.keys():
        confusions[LABEL_LST[i]] = []
    if cm_model[i, j] > thresh:
        confusions[LABEL_LST[i]].append(LABEL_LST[j])
    
    if cm_model[i, j] > thresh and LABEL_LST[i] != 'no_relation' and LABEL_LST[j] != 'no_relation':
        if cm_model[i, j] > cm_spanbert[i,j] :
            print("\033[91m {}, {}, {}, {}\033[00m".format(LABEL_LST[i], LABEL_LST[j], cm_model[i, j], cm_spanbert[i,j]))
        else:
            print("\033[92m {}, {}, {}, {}\033[00m".format(LABEL_LST[i], LABEL_LST[j], cm_model[i, j], cm_spanbert[i,j]))

relation_df['confused_with:'] = relation_df['relation'].map(confusions)


These are the relations that most commonly get mistaken for one another (barring confusions with no_relaiton)
TRUE:  , PRED:  , MODEL numerr:  , SPANBERT numerr: 
 per:title, per:employee_of, 2, 2
 org:top_members/employees, org:founded_by, 9, 6
 org:top_members/employees, org:shareholders, 4, 1
 per:employee_of, per:title, 2, 2
 per:employee_of, per:countries_of_residence, 2, 2
 per:employee_of, per:schools_attended, 4, 0
 org:alternate_names, org:top_members/employees, 3, 0
 org:alternate_names, org:subsidiaries, 2, 3
 org:country_of_headquarters, per:countries_of_residence, 3, 1
 org:country_of_headquarters, per:origin, 6, 7
 per:countries_of_residence, per:origin, 2, 8
 org:city_of_headquarters, org:top_members/employees, 5, 0
 org:city_of_headquarters, per:cities_of_residence, 3, 2
 org:city_of_headquarters, org:founded_by, 2, 0
 per:cities_of_residence, per:city_of_death, 6, 2
 per:stateorprovinces_of_residence, per:cities_of_residence, 4, 1
 per:stateorprovinces_of_residence, pe

In [160]:
thresh = 5
print("These are the relations that most commonly get mistaken for one another (barring confusions with no_relaiton)")
print("TRUE: ", ", PRED: ", ", MODEL numerr: ", ", SPANBERT numerr: ")
confusions = {}
for i, j in itertools.product(range(cm_model.shape[0]), range(cm_model.shape[1])):
    if LABEL_LST[i] not in confusions.keys():
        confusions[LABEL_LST[i]] = []
    if cm_model[i, j] > thresh:
        confusions[LABEL_LST[i]].append(LABEL_LST[j])
    
    if cm_model[i, j] > thresh and LABEL_LST[i] != 'no_relation' and LABEL_LST[j] == 'no_relation':
        if cm_model[i, j] > cm_spanbert[i,j] :
            print("\033[91m {}, {}, {}, {}\033[00m".format(LABEL_LST[i], LABEL_LST[j], cm_model[i, j], cm_spanbert[i,j]))
        else:
            print("\033[92m {}, {}, {}, {}\033[00m".format(LABEL_LST[i], LABEL_LST[j], cm_model[i, j], cm_spanbert[i,j]))

relation_df['confused_with:'] = relation_df['relation'].map(confusions)

These are the relations that most commonly get mistaken for one another (barring confusions with no_relaiton)
TRUE:  , PRED:  , MODEL numerr:  , SPANBERT numerr: 
 per:title, no_relation, 90, 70
 org:top_members/employees, no_relation, 51, 66
 per:employee_of, no_relation, 121, 113
 org:alternate_names, no_relation, 63, 30
 org:country_of_headquarters, no_relation, 102, 73
 per:countries_of_residence, no_relation, 37, 43
 org:city_of_headquarters, no_relation, 42, 26
 per:cities_of_residence, no_relation, 29, 22
 per:age, no_relation, 14, 27
 per:stateorprovinces_of_residence, no_relation, 15, 16
 per:origin, no_relation, 51, 42
 org:subsidiaries, no_relation, 56, 52
 org:parents, no_relation, 31, 44
 per:spouse, no_relation, 38, 31
 org:stateorprovince_of_headquarters, no_relation, 19, 15
 per:children, no_relation, 19, 9
 per:other_family, no_relation, 10, 10
 per:alternate_names, no_relation, 20, 15
 org:members, no_relation, 18, 7
 per:siblings, no_relation, 8, 1
 per:schools_atten

In [161]:
# Sanity Check
# TODO:   ['Mohammed bin Rashid Al Maktoum', 'UNK', 'UNK']    why are two of the three slots 'UNK'?
sub_df = df_errors[df_errors['relation'] == 'per:origin']
sub_df = sub_df[sub_df['prediction_model'] == 'per:countries_of_residence']
print(sub_df.shape[0])
#print(sub_df[['example', 'subj', 'obj', 'subj_mentions', 'obj_mentions']])

51


# Looking at the Separation between subj and obj

Is it more difficult if the subj and obj are further spread apart in the example? Does it make a difference whether it's subj->obj vs. obj->subj?

# Are the exmples with more entities/mentions in the example more difficult?

In [162]:
###### NUM ENTITIES ######
print()
print("FULL model prop ner entities: ", df_results['prop_ner'].mean())
print("ERRS model prop ner entities: ", df_errors['prop_ner'].mean())

print()
print("FULL_spanbert prop ner entities: ", df_results_spanbert['prop_ner'].mean())
print("ERRS_spanbert prop ner entities: ", df_errors_spanbert['prop_ner'].mean())



FULL model prop ner entities:  0.23738384152166184
ERRS model prop ner entities:  0.25336314681081934

FULL_spanbert prop ner entities:  0.23738384152166184
ERRS_spanbert prop ner entities:  0.2494788798312678


In [163]:
###### NUM MENTIONS ######
print()
print("FULL prop boot mentions: ", df_results['prop_mentions'].mean())
print("ERRS model prop boot mentions: ", df_errors['prop_mentions'].mean())
print("ERRS spanbert prop boot mentions: ", df_errors_spanbert['prop_mentions'].mean())


FULL prop boot mentions:  0.26010009298476244
ERRS model prop boot mentions:  0.2746156976402246
ERRS spanbert prop boot mentions:  0.2746542779258415


# For the examples our model gets, but the baseline (vanilla) model misses, why does bootleg help?

We want to confirm that the improvement ties back to insights in bootleg - i.e., the mentions/types/relations in bootleg's database.

In [164]:
# get the set difference of errors
df_spanbert_not_model_errors = df_errors_spanbert[~df_errors_spanbert['id'].isin(df_errors['id'])]
df_model_not_spanbert_errors = df_errors[~df_errors['id'].isin(df_errors_spanbert['id'])]
print("The #examples our model improves on vs. baseline are: ", df_spanbert_not_model_errors.shape[0])
print("The #examples our model does worse on vs. baseline are: ", df_model_not_spanbert_errors.shape[0])
# df_vanilla_not_model_errors.to_csv('vanilla_not_model_errors.csv', sep='\t')
# df_model_not_vanilla_errors.to_csv('model_not_vanilla_errors.csv', sep='\t')

for i, row in df_spanbert_not_model_errors.iterrows():
    print(row)
    print()
    if i == 10:
        break

The #examples our model improves on vs. baseline are:  786
The #examples our model does worse on vs. baseline are:  1438
obj                    ['turku']                                                                                                                                                                                                                                                                                       
obj_mentions           ['Perno shipyard']                                                                                                                                                                                                                                                                              
subj_qids              ['Q1524298', 'Q1524298']                                                                                                                                                                                                                

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [165]:
# THE DISTRIBUTION of RELATIONS WHEN MODEL IMPOVES OVER SPANBERT
print("THE DISTRIBUTION of RELATIONS WHEN MODEL IMPROVES OVER SPANBERT")
relations_errs_matchqids = []
for index, row in df_spanbert_not_model_errors.iterrows():
    relations_errs_matchqids.append(row['relation'])
print(Counter(relations_errs_matchqids))
print()

# THE DISTRIBUTION OF RELATIONS WHEN SPANBERT IMPROVES OVER MODEL
print(" THE DISTRIBUTION OF RELATIONS WHEN SPANBERT IMPROVES OVER MODEL")
relations_errs_matchqids = []
for index, row in df_model_not_spanbert_errors.iterrows():
    relations_errs_matchqids.append(row['relation'])
print(Counter(relations_errs_matchqids))


THE DISTRIBUTION of RELATIONS WHEN MODEL IMPROVES OVER SPANBERT
Counter({'no_relation': 427, 'org:top_members/employees': 44, 'per:title': 40, 'per:employee_of': 39, 'per:countries_of_residence': 28, 'per:age': 23, 'per:city_of_death': 18, 'per:cause_of_death': 16, 'org:parents': 15, 'per:cities_of_residence': 14, 'per:charges': 12, 'per:religion': 11, 'per:date_of_death': 10, 'per:stateorprovinces_of_residence': 9, 'org:subsidiaries': 8, 'org:country_of_headquarters': 8, 'per:spouse': 7, 'org:shareholders': 7, 'per:stateorprovince_of_birth': 6, 'org:website': 6, 'per:other_family': 5, 'per:origin': 5, 'org:stateorprovince_of_headquarters': 5, 'per:country_of_birth': 4, 'org:number_of_employees/members': 4, 'per:stateorprovince_of_death': 3, 'per:parents': 3, 'per:children': 2, 'per:siblings': 2, 'per:city_of_birth': 1, 'org:members': 1, 'org:founded_by': 1, 'org:political/religious_affiliation': 1, 'org:city_of_headquarters': 1})

 THE DISTRIBUTION OF RELATIONS WHEN SPANBERT IMPROVES 

### When the subj and obj qid match this tends to indicate alternate names --- bootleg doesn't do well on alternate names --- how does spanbert do?

In [166]:
count_errors = 0
relations_errs_matchqids = []
for index, row in df_errors_spanbert.iterrows():
    # subj qid
    subj_qids_str = row['subj_qids']
    subj_qids = ast.literal_eval(subj_qids_str)
    subj_qid = subj_qids[0]
    
    # obj qid
    obj_qids_str = row['obj_qids']
    obj_qids = ast.literal_eval(obj_qids_str)
    obj_qid = obj_qids[0]
    
    if subj_qid == obj_qid and subj_qid != 'UNK':
        count_errors += 1
        relations_errs_matchqids.append(row['relation'])
count_errors
print(Counter(relations_errs_matchqids))

count_results = 0
relations_matchqids = []
for index, row in df_results_spanbert.iterrows():
    # subj qid
    subj_qids_str = row['subj_qids']
    subj_qids = ast.literal_eval(subj_qids_str)
    subj_qid = subj_qids[0]
    
    # obj qid
    obj_qids_str = row['obj_qids']
    obj_qids = ast.literal_eval(obj_qids_str)
    obj_qid = obj_qids[0]
    
    if subj_qid == obj_qid and subj_qid != 'UNK':
        count_results += 1
        relations_matchqids.append(row['relation'])
        
print(Counter(relations_matchqids))
count_results

error_rate_orig = df_errors_spanbert.shape[0]/df_results_spanbert.shape[0]
error_rate_new = (df_errors_spanbert.shape[0]-count_errors)/df_results_spanbert.shape[0]
print("original number of errors: ", df_errors.shape[0])
print("total instances of two matching qids subj and obj: ", count_results)
print("corrected errors: ", count_errors)
print(error_rate_orig)
print(error_rate_new)

Counter({'no_relation': 26, 'org:alternate_names': 13, 'per:alternate_names': 9, 'org:subsidiaries': 8, 'org:parents': 3, 'org:founded_by': 1})
Counter({'org:alternate_names': 187, 'no_relation': 181, 'org:subsidiaries': 15, 'per:alternate_names': 12, 'per:children': 6, 'per:parents': 4, 'org:parents': 3, 'org:founded_by': 1, 'per:employee_of': 1, 'per:spouse': 1, 'per:cities_of_residence': 1})
original number of errors:  2596
total instances of two matching qids subj and obj:  412
corrected errors:  60
0.08589987185718705
0.0832486412443109


### SPANBERT WORSE THAN BOOTLEG

Here we find that the *number* of proper nouns that have errors and receive bootleg mentions are about the same w/ vs. w/out using bootleg entity embeddings. 

In [167]:
# some constants
proper_noun = ['NNP', 'NNPS']
nonproper_noun = ['NN', 'NNS']
number_pos = ['CD']
nomention = ["['UNK']", "['UNK', 'UNK']", "['UNK', 'UNK', 'UNK']", "['UNK', 'UNK', 'UNK', 'UNK']", 
             "['UNK', 'UNK', 'UNK', 'UNK', 'UNK']"]
cols = ['example', 'relation','prediction_model', 'prediction_spanbert', 'mentions', 'subj_pos', 'obj_pos', 'subj', 'obj', 'subj_mentions', 'subj_qids', 'obj_mentions', 'obj_qids', 'id']

In [174]:
def get_relations(subj_qids_str, obj_qids_str):
    subj_qids = ast.literal_eval(subj_qids_str)
    obj_qids = ast.literal_eval(obj_qids_str)
    subj_qid = subj_qids[0]
    obj_qid = obj_qids[0]
    
    rels = [esp.get_relation_name(r) for r in esp.get_all_relations(subj_qid, obj_qid)]
    rels = [rel_to_name.get(rel, rel) for rel in rels]
    return rels

In [175]:
def get_related_entities(qid):
    # Get all connected qids for a given qid
    related_qids = du.get_related_qids(qid, es)
    print(f"Related QIDs {related_qids}")
    print([es.get_title(qid) for qid in related_qids])

    lst = [es.get_title(qid) for qid in related_qids]

In [176]:
lst_pos_subj_spanbert = []
lst_subj_nomention_spanbert = {}
lst_pos_obj_spanbert = []
lst_obj_nomention_spanbert = {}

sub_df = df_spanbert_not_model_errors[cols]
for index, row in sub_df.iterrows():
    if any(pos in row['subj_pos'] for pos in proper_noun): # is the subj a proper noun?
        lst_pos_subj_spanbert.append(row['subj'])
        if any(null in row['subj_mentions'] for null in nomention): # is the bootleg mention empty for this proper noun?
            lst_subj_nomention_spanbert[row['id']] = row['subj']
            
    if any(pos in row['obj_pos'] for pos in proper_noun):
        lst_pos_obj_spanbert.append(row['obj'])
        if any(null in row['obj_mentions'] for null in nomention):
            lst_obj_nomention_spanbert[row['id']] = row['obj']
        
print("The number of proper noun subj in spanbert errors are:", len(lst_pos_subj_spanbert), "and obj are:", len(lst_pos_obj_spanbert))
print("The number of proper noun subj in spanbert errors that don't get a bootleg mention are:", len(lst_subj_nomention_spanbert.keys()), "and obj are:", len(lst_obj_nomention_spanbert.keys()))
print()

lst_pos_subj_spanbert.extend(lst_pos_obj_spanbert)
print("SPANBERT DOES WORSE THAN BOOTLEG MODEL ON THESE SUBJ/OBJ PROPER NOUNS, THIS MANY TIMES:")#print(len(lst_pos_subj_spanbert))
worst_for_spanbert = Counter(lst_pos_subj_spanbert).most_common(50)
print(worst_for_spanbert)
worst_for_spanbert = [tup[0] for tup in worst_for_spanbert]


The number of proper noun subj in spanbert errors are: 570 and obj are: 496
The number of proper noun subj in spanbert errors that don't get a bootleg mention are: 25 and obj are: 50

SPANBERT DOES WORSE THAN BOOTLEG MODEL ON THESE SUBJ/OBJ PROPER NOUNS, THIS MANY TIMES:
[("['millipore']", 14), ("['galleon', 'group']", 14), ("['eta']", 13), ("['france']", 13), ("['david', 'gutierrez']", 12), ("['maria', 'kaczynska']", 12), ("['burlington', 'northern', 'santa', 'fe', 'corp.']", 11), ("['rosoboronexport']", 10), ("['orlando', 'zapata']", 9), ("['mathieu', 'montcourt']", 9), ("['anwar', 'chowdhry']", 9), ("['united', 'states']", 9), ("['saturday']", 9), ("['stuart', 'rose']", 8), ("['marshall']", 8), ("['nuclear', 'energy', 'institute']", 8), ("['mohammed', 'sayed', 'tantawi']", 8), ("['keli', 'mcgregor']", 8), ("['thomas', 'more', 'law', 'center']", 8), ("['new', 'york']", 8), ("['u.s.']", 8), ("['marc', 'bolland']", 7), ("['arcandor']", 7), ("['orlando', 'zapata', 'tamayo']", 7), ("['ac

In [193]:
# Inspecting examples where bootleg had any relation for the subj, obj pair

count = 0
for index, row in df_errors_spanbert.iterrows():
    if get_relations(row['subj_qids'], row['obj_qids']):
        count += 1
print("For ", count, " spanbert errors, bootleg has *some* relation between the subj and obj")

count = 0
for index, row in df_results_spanbert.iterrows():
    rels = get_relations(row['subj_qids'], row['obj_qids'])
    if rels and not any(rel for rel in rels if rel in row['relation']):
        print(row[['example', 'subj', 'obj', 'subj_qids', 'obj_qids', 'relation', 'prediction_model', 'prediction_spanbert', 'mentions']])
        print(f"Rels {rels}")
        print()
        count += 1

print("For ", count, " spanbert errors, the existing bootleg relation is NOT a subset of the gold relation")


For  356  spanbert errors, bootleg has *some* relation between the subj and obj
example                former aiba president anwar chowdhry of pakistan , who was ousted last year after two decades in power , was declared `` ineligible for life '' and could face legal action from aiba to recover allegedly embezzled funds .                                                                                                                                                                       
subj                   ['anwar', 'chowdhry']                                                                                                                                                                                                                                                                                                                                                                              
obj                    ['pakistan']                                                               

example                marks and spencer chairman stuart rose said the group was facing a `` third dab -lrb- touch -rrb- of the brakes '' since economic worries emerged last year in the wake of a global squeeze on credit and britain 's slowing housing market .                                                                                                                                                                                                                                       
subj                   ['stuart', 'rose']                                                                                                                                                                                                                                                                                                                                                                                                                                                                  
obj             

Name: 1599, dtype: object
Rels ['member of']

example                al-hakim said the criticisms of the shiite-dominated government ignored the accomplishments of iraq since the overthrow of saddam hussein 's sunni-led regime , and he told other nations not to try to push iraq around .                                                                                                                  
subj                   ['al-hakim']                                                                                                                                                                                                                                                                                                                                
obj                    ['iraq']                                                                                                                                                                                                                   

Name: 2414, dtype: object
Rels ['country of citizenship']

example                baa agreed last month to sell london gatwick airport to global infrastructure partners for 1.5 billion pounds .                                                                                                                                                                     
subj                   ['global', 'infrastructure', 'partners']                                                                                                                                                                                                                                            
obj                    ['london', 'gatwick']                                                                                                                                                                                                                                                               
subj_qids              ['Q5570413', 'Q557

example                `` the target of reducing the total number of centrally - administered soes to 80 to 100 by 2010 is unchanged , '' said li rongrong , chairman of the state-owned assets supervision and administration commission -lrb- sasac -rrb- , at a press conference at the beijing international media center .                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
subj                   ['sasac']                                                                                                       

...

example                truffaut , godard , rohmer , rivette , chabrol , varda ... and new wave related guys like resnais , marker , etc. .                                                                                                                                                       
subj                   ['chabrol']                                                                                                                                                                                                                                                               
obj                    ['new', 'wave']                                                                                                                                                                                                                                                           
subj_qids              ['Q55375']                                                                                                 

example                a spokesman for state-run arms exporter rosoboronexport had no comment ; no one answered the phones at the venezuelan embassy in moscow .                                                                              
subj                   ['rosoboronexport']                                                                                                                                                                                                    
obj                    ['moscow']                                                                                                                                                                                                             
subj_qids              ['Q1353090']                                                                                                                                                                                                           
obj_qids               ['Q649']             

example                bejarano rode stakes winners with three mounts in a row -- saint anddan -lrb- 8-1 -rrb- for trainer bobby frankel in the 7-furlong churchill downs stakes , 7-2 take the ribbon for wally dollase in the 1-mile-on-turf churchill distaff turf mile , and 7-1 hystericalady for jerry hollendorfer in the 7-furlong humana distaff .                                                                                                                                                                                                                                                                                                       
subj                   ['bobby', 'frankel']                                                                                                                                                                                                                                                                                                                          

example                the recent round of sanctions imposed by the un security council against iran 's controversial nuclear issue has `` no affect on our decision-making processes , '' ahmadinejad said after he attended the 11th summit of the economic cooperation organization -lrb- eco -rrb- held here .                                                                                                                                                                                                                                                                                                                                                                                           
subj                   ['eco']                                                                                                                                                                                                                                                                                            

example                last week , a federal grand jury formally indicted rajaratnam , the billionaire founder of the galleon group , and chiesi , of new castle partners , on many counts of securities fraud and conspiracy .                                                                                                                                                                                                                             
subj                   ['galleon', 'group']                                                                                                                                                                                                                                                                                                                                                                                                                 
obj                    ['rajaratnam']                                                                         

In [178]:
# Inspecting examples where bootleg had a relation for the subj, obj pair
# booterrors_with_relation_df = df_errors[df_errors['id'].isin(ids_missed_propernoun_with_bootrels)]
count = 0
for index, row in df_spanbert_not_model_errors.iterrows():
    rels = get_relations(row['subj_qids'], row['obj_qids'])
    if rels and any(rel for rel in rels if rel in row['relation']):
        print(row[['example', 'subj', 'obj', 'subj_qids', 'obj_qids', 'relation', 'prediction_model', 'prediction_spanbert', 'mentions']])
        print(f"Rels {rels}")
        print()
        count += 1
        
print("For ", count, " spanbert errors, the bootleg relation is a subset (or the same) as the gold relation")


example                title : aaas science & technology policy fellowships department : aaas science & technology policy fellowships employer : aaas location : washington , dc , united states posted : oct 23                                                                                                                                                                                                                                                                                                                                 
subj                   ['aaas', 'science', '&', 'technology', 'policy', 'fellowships', 'department']                                                                                                                                                                                                                                                                                                                                                                                  

In [179]:
# Inspecting examples where bootleg had a relation for the subj, obj pair
# booterrors_with_relation_df = df_errors[df_errors['id'].isin(ids_missed_propernoun_with_bootrels)]
count = 0
for index, row in df_errors_spanbert.iterrows():
    rels = get_relations(row['subj_qids'], row['obj_qids'])
    if rels and any(rel for rel in rels if rel in row['prediction_spanbert']):
        print(row[['example', 'subj', 'obj', 'subj_qids', 'obj_qids', 'relation', 'prediction_model', 'prediction_spanbert', 'mentions']])
        print(f"Rels {rels}")
        print()
        count += 1
        
print("For ", count, " spanbert errors, the bootleg relation is a subset (or the same) as the spanbert prediction")


example                a study by the international water management institute -lrb- iwmi -rrb- in sri lanka warns that ethanol production in india and china would severely impact the two countries ' water supplies .                                                                                                                                                                                                                                                 
subj                   ['iwmi']                                                                                                                                                                                                                                                                                                                                                                                                                                          
obj                    ['sri', 'lanka']                                             

example                the usw represents about 1.2 million active and retired members in the united states and canada .                                                             
subj                   ['usw']                                                                                                                                                       
obj                    ['united', 'states']                                                                                                                                          
subj_qids              ['Q494197']                                                                                                                                                   
obj_qids               ['Q30', 'Q30']                                                                                                                                                
relation               no_relation                                                        

### FOR EXAMPLES WHERE SPANBERT IS BETTER THAN BOOTLEG

In [180]:
lst_pos_subj_model = []
lst_subj_nomention_model = {}
lst_pos_obj_model = []
lst_obj_nomention_model= {}

sub_df = df_model_not_spanbert_errors[cols]
for index, row in sub_df.iterrows():
    if any(pos in row['subj_pos'] for pos in proper_noun): # is the subj a proper noun?
        lst_pos_subj_model.append(row['subj'])
        if any(null in row['subj_mentions'] for null in nomention): # is the bootleg mention empty for this proper noun?
            lst_subj_nomention_model[row['id']] = row['subj']
            
    if any(pos in row['obj_pos'] for pos in proper_noun):
        lst_pos_obj_model.append(row['obj'])
        if any(null in row['obj_mentions'] for null in nomention):
            lst_obj_nomention_model[row['id']] = row['obj']
        
print("The number of proper noun subj in bootleg (&not spanbert) errors are:", len(lst_pos_subj_spanbert), "and obj are:", len(lst_pos_obj_spanbert))
print("The number of proper noun subj in bootleg (&not spanbert) errors that don't get a bootleg mention are:", len(lst_subj_nomention_spanbert.keys()), "and obj are:", len(lst_obj_nomention_spanbert.keys()))
print()

lst_pos_subj_model.extend(lst_pos_obj_model)
print("SPANBERT DOES BETTER THAN BOOTLEG MODEL ON THESE SUBJ/OBJ PROPER NOUNS")#print(len(lst_pos_subj_spanbert))
worst_for_model = Counter(lst_pos_subj_model).most_common(50)
print(worst_for_model)
worst_for_model = [tup[0] for tup in worst_for_model]

The number of proper noun subj in bootleg (&not spanbert) errors are: 1066 and obj are: 496
The number of proper noun subj in bootleg (&not spanbert) errors that don't get a bootleg mention are: 25 and obj are: 50

SPANBERT DOES BETTER THAN BOOTLEG MODEL ON THESE SUBJ/OBJ PROPER NOUNS
[("['julius', 'baer']", 28), ("['access', 'industries']", 19), ("['thomas', 'more', 'law', 'center']", 18), ("['galleon', 'group']", 18), ("['american', 'association', 'for', 'the', 'advancement', 'of', 'science']", 18), ("['france']", 18), ("['stuart', 'rose']", 17), ("['bipartisan', 'policy', 'center']", 17), ("['girija', 'prasad', 'koirala']", 17), ("['eco']", 16), ("['tahawwur', 'hussain', 'rana']", 15), ("['rosoboronexport']", 15), ("['douglas', 'flint']", 15), ("['u.s.']", 15), ("['burlington', 'northern', 'santa', 'fe', 'corp.']", 14), ("['washington', 'national', 'opera']", 14), ("['aaas']", 13), ("['arcandor']", 13), ("['anwar', 'chowdhry']", 13), ("['clifton']", 13), ("['hewitt']", 13), ("['gwat

In [181]:
# model_worse_than_spanbert = [tup for tup in worst_for_model if tup not in worst_for_spanbert]
# for item in model_worse_than_spanbert:
#     item = ast.literal_eval(item)
#     item = ' '.join(item)
#     cands = get_candidates(item)
#     print("Cands for ", item, " are: ", f"Cands {cands}", "\n")

In [182]:
sub_df = df_model_not_spanbert_errors[cols] #BOOTLEG ERRORS, and NOT BASELINE ERRORS
count_missed_propernoun = 0
count_missed_propernoun_with_bootrels = 0
ids_missed_propernoun_with_bootrels = []
for index, row in sub_df.iterrows():
    if any(pos in row['subj_pos'] for pos in proper_noun) or any(pos in row['obj_pos'] for pos in proper_noun):
#        print(row[['example', 'subj', 'obj', 'subj_qids', 'obj_qids', 'relation', 'prediction_model', 'prediction_spanbert', 'mentions']])
        rels = get_relations(row['subj_qids'], row['obj_qids'])
        if rels:
            count_missed_propernoun_with_bootrels += 1
            ids_missed_propernoun_with_bootrels.append(row['id'])
#         print(f"Rels {rels}")
#         print()
        count_missed_propernoun += 1
        
print("Number of examples where bootleg had a relation for the subj, obj pair: ", count_missed_propernoun_with_bootrels)
print("Number of examples where subj and/or obj is a proper noun: ", count_missed_propernoun)


Number of examples where bootleg had a relation for the subj, obj pair:  161
Number of examples where subj and/or obj is a proper noun:  1310


In [183]:
# Inspecting examples where bootleg had any relation for the subj, obj pair
# booterrors_with_relation_df = df_errors[df_errors['id'].isin(ids_missed_propernoun_with_bootrels)]
count = 0
for index, row in df_results.iterrows():
    if get_relations(row['subj_qids'], row['obj_qids']):
        count += 1
print("For ", count, " bootleg errors, bootleg has *some* relation between the subj and obj\n")


print("For these bootleg errors, the existing bootleg relation is NOT a string-subset of the gold relation")
count = 0
for index, row in df_results.iterrows():
    rels = get_relations(row['subj_qids'], row['obj_qids'])
    if rels and not any(rel for rel in rels if rel in row['relation']):
#         print(row[['example', 'subj', 'obj', 'subj_qids', 'obj_qids', 'relation', 'prediction_model', 'prediction_spanbert', 'mentions']])
#         print(f"Rels {rels}")
#         print()
        count += 1

print("For ", count, " bootleg errors, the existing bootleg relation is NOT a subset of the gold relation")


For  1558  bootleg errors, bootleg has *some* relation between the subj and obj

For these bootleg errors, the existing bootleg relation is NOT a string-subset of the gold relation
For  1420  bootleg errors, the existing bootleg relation is NOT a subset of the gold relation


In [184]:
# Inspecting examples where bootleg had a relation for the subj, obj pair
# booterrors_with_relation_df = df_errors[df_errors['id'].isin(ids_missed_propernoun_with_bootrels)]
count = 0
for index, row in df_errors.iterrows():
    rels = get_relations(row['subj_qids'], row['obj_qids'])
    if rels and any(rel for rel in rels if rel in row['relation']):
        print(row[['example', 'subj', 'obj', 'subj_qids', 'obj_qids', 'relation', 'prediction_model', 'prediction_spanbert', 'mentions']])
        print(f"Rels {rels}")
        print()
        count += 1
        
print("For ", count, " bootleg errors, the bootleg relation is a subset (or the same) as the gold relation")


example                dunne 's brother was the writer john gregory dunne , the husband of the writer joan didion .                                                                                                          
subj                   ['dunne']                                                                                                                                                                                             
obj                    ['john', 'gregory', 'dunne']                                                                                                                                                                          
subj_qids              ['Q448767']                                                                                                                                                                                           
obj_qids               ['Q705022', 'Q705022', 'Q705022']                                                        

example                -- dow jones newswires contributed to this story -- on the chinese side , the agreements were signed by the china banking regulatory commission , the china insurance regulatory commission and the china securities regulatory commission .                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
subj                   ['china', 'banking', 'regulatory', 'commission']                                                                                                                                                                                              

Name: 11402, dtype: object
Rels ['sibling']

example                al-hakim 's death could severely weaken his party , raising concerns that some of its supporters could turn to more radical figures like al-sadr and otherwise stir up the already uncertain politics among the shiite community .                                                                                         
subj                   ['al-hakim']                                                                                                                                                                                                                                                                                                               
obj                    ['shiite']                                                                                                                                                                                                                                                    

Name: 18942, dtype: object
Rels ['country']

example                alcoa _ alcoa reached a tentative agreement with the united steelworkers union that may avert a strike by almost 6,000 workers across the united states .                                                                                                                                                                 
subj                   ['united', 'steelworkers']                                                                                                                                                                                                                                                                                                
obj                    ['united', 'states']                                                                                                                                                                                                                                            

example                ----- ===== 0 ===== ----- co-authors are : julio betancourt and robert hirsch at the u.s. geological survey , malin falkenmark at the stockholm international water institute in sweden , zbigniew kundzewicz at the potsdam institute for climate impact research in germany ronald stouffer at the geophysical fluid dynamics laboratory in princeton , n.j. .                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 

In [185]:
# Inspecting examples where bootleg had a relation for the subj, obj pair
# booterrors_with_relation_df = df_errors[df_errors['id'].isin(ids_missed_propernoun_with_bootrels)]
count = 0
for index, row in df_errors.iterrows():
    rels = get_relations(row['subj_qids'], row['obj_qids'])
    if rels and any(rel for rel in rels if rel in row['prediction_model']):
        print(row[['example', 'subj', 'obj', 'subj_qids', 'obj_qids', 'relation', 'prediction_model', 'prediction_spanbert', 'mentions']])
        print(f"Rels {rels}")
        print()
        count += 1
        
print("For ", count, " bootleg errors, the bootleg relation is a subset (or the same) as the bootleg prediction")


example                but sistani and al-hakim are unwise to allow themselves to be used this way by bush , since their political standing with the shiite public will certainly suffer greatly as a result .                                                                                         
subj                   ['al-hakim']                                                                                                                                                                                                                                                                    
obj                    ['shiite']                                                                                                                                                                                                                                                                      
subj_qids              ['Q4115267']                                                                             

example                switzerland could gain thousands of jobs if the proposal is accepted , said urs roth , chief executive of the swiss bankers association .                                                                                                                                                                 
subj                   ['swiss', 'bankers', 'association']                                                                                                                                                                                                                                                                       
obj                    ['switzerland']                                                                                                                                                                                                                                                                                           
subj_qids              ['Q798804',

#### For these proper nouns that don't get a bootleg mention, is it because they are not in bootleg's database?

In [186]:
#print(lst_subj_nomention_model)

no_candidates_values = []
has_candidates_values = []
# alias is the subj/obj that did not receive a bootleg mention
for idx, value in lst_subj_nomention_model.items():
    row = df_results[df_results['id'] == idx]   
    value = ast.literal_eval(value)
    alias = " ".join(value)
    try:
        cands = esp.get_qid_cands(alias)
        #print("{}\n{}\n{}\n\n".format(row['example'], alias, f"Cands {cands}") # uncomment to view the alias in context downstream
        has_candidates_values.append(alias)
    except: 
        no_candidates_values.append(alias)

print("Of these values that received no bootleg mention,", len(has_candidates_values), "(total)/", len(set(has_candidates_values)), "(unique), ARE IN the bootleg database.")

######## THIS SET OF ENTITIES SIMPLY DON'T HAVE CANDIDATES FOR THEM IN BOOTLEG! WE SHOULD ADD THEM! ############
print("Of these values that received no bootleg mention,", len(no_candidates_values), "(total)/", len(set(no_candidates_values)), "(unique), ARE NOT IN the bootleg database.")
print()
print(set(no_candidates_values))


Of these values that received no bootleg mention, 11 (total)/ 3 (unique), ARE IN the bootleg database.
Of these values that received no bootleg mention, 39 (total)/ 11 (unique), ARE NOT IN the bootleg database.

{'oudeh', 'election complaints commission', 'wno', 'banking regulatory commission', 'attenti holdings', 'economic cooperation organisation', 'southgobi energy resources', 'millipore', 'karrera sarobe', 'millipore corp.', 'millipore corp'}


In [187]:
# TODO: whether check the type of the subject and object to see if it aligns wiht the relation. 
# e.g. PARIS went to PARIS -- do the types of the entities TYPECHECK (i.e. person, location, organization) -- i.e. a location cannot go to an organzation 
# if "X" in sentence, it cannot be "Y" relation -- we want to do this in a systematic way


# If I fix this bucket, what score would I expect. Modular function. -- 

#### Error rates for words

In [188]:
nomention_model_not_spanbert = []
sub_df = df_model_not_spanbert_errors[cols]
for index, row in sub_df.iterrows():
    qids = row['mentions']
    qids = ast.literal_eval(qids)
    words = row['example'].split(' ')
    for i in range(len(words)):
        if qids[i] == 'UNK' and words[i] not in stop_words and words[i] not in punctuation:
            nomention_model_not_spanbert.append(words[i])

print("WORSE FOR MODEL THAN SPANBERT")
ctr_nomention = Counter(nomention_model_not_spanbert).most_common(50)
print(ctr_nomention)


nomention_spanbert_or_model = []
sub_df = df_spanbert_not_model_errors[cols]
for index, row in sub_df.iterrows():
    qids = row['mentions']
    qids = ast.literal_eval(qids)
    words = row['example'].split(' ')
    for i in range(len(words)):
        if qids[i] == 'UNK' and words[i] not in stop_words and words[i] not in punctuation:
            nomention_spanbert_or_model.append(words[i])
            
print("WORSE FOR SPANBERT THAN MODEL")
print(Counter(nomention_spanbert_or_model).most_common(50))


WORSE FOR MODEL THAN SPANBERT
[('said', 323), ('-rrb-', 251), ('-lrb-', 238), ('died', 94), ('former', 92), ('two', 88), ('years', 86), ('billion', 79), ('one', 78), ('company', 76), ('wife', 75), ('death', 64), ('$', 64), ('president', 64), ('million', 59), ('year', 56), ('also', 56), ('last', 54), ('first', 54), ('born', 53), ('would', 53), ('since', 53), ('group', 52), ('son', 51), ('percent', 49), ('leader', 45), ('three', 45), ('new', 43), ('us', 42), ('head', 42), ('whose', 41), ('top', 40), ('dollars', 39), ('spokesman', 38), ('wednesday', 37), ('members', 37), ('family', 37), ('including', 37), ('statement', 36), ('monday', 36), ('director', 36), ('found', 35), ('cancer', 35), ('home', 35), ('made', 35), ('became', 35), ('known', 34), ('tuesday', 33), ('according', 33), ('called', 33)]
WORSE FOR SPANBERT THAN MODEL
[('said', 170), ('-rrb-', 93), ('-lrb-', 92), ('died', 77), ('president', 51), ('$', 42), ('group', 41), ('home', 41), ('new', 39), ('billion', 38), ('years', 36), (

In [189]:
errates_model = {}
for index, row in df_results.iterrows():
    err = 0
    if row['relation'] != row['prediction_model']:
        err = 1
    words = row['example'].split(' ')
    for i in range(len(words)):
        if words[i] in errates_model:
            errates_model[words[i]]['count'] += 1
            errates_model[words[i]]['errs'] += err
        else:
            errates_model[words[i]] = {}
            errates_model[words[i]]['count'] = 1
            errates_model[words[i]]['errs'] = err

for k, v in errates_model.items():
    errates_model[k]['errrate'] = errates_model[k]['errs']/errates_model[k]['count'] 
    if errates_model[k]['errrate'] > 0.9:
        print(k)


2009-07-07
11:07:32
militarisation
michigan-born
2010-02-03
10:30:10
unaffected
3,700
audible
infidels
elevates
narrate
bruised
opportunism
formulating
implicitly
quran
sunna
umbilical
cords
blood-forming
weissman
inmate
humanely
tessa
docklands
short-haul
destinations
recognize
estuaries
furnace
tomoya
kawakita
commuted
irritates
then-president
adl
savvy
overthrow
channeled
soaking
enhances
inability
scenarios
over-exploitation
tushaar
shirlee
unveils
exhaustive
unwise
suffer
upendra
moller
fahim
thishers
abstract
57,000
inaugural
annouce
483
70.7
end-january
14.3
243
paramananda
jha
hindi
hemanta
rawal
18:13:33
reclaimed
574
314
co-chief
kensington
id8dbqfg8ty
iz2i76ou9wqrapinakcnv6nc5njmpbs8cv1ngtrstv2j7acgovyi
hmgemmmpx7gxoag057lfdmu
hwl5
pgp
acn
delegations
thumbs
waged
demonstration
ri
dong-sam
reconnaissance
sici
montemerlo
figurehead
well-armed
francie
schulwolf
consolidated
silesian
74
berri
jawad
377
rocked
north-central
1800
roald
09
essays
bloodthirsty
bln
waziri
377,000
00

In [190]:
errates_spanbert = {}
for index, row in df_results.iterrows():
    err = 0
    if row['relation'] != row['prediction_spanbert']:
        err = 1
    words = row['example'].split(' ')
    for i in range(len(words)):
        if words[i] not in punctuation and words[i] not in stop_words:
            if words[i] in errates_spanbert:
                errates_spanbert[words[i]]['count'] += 1
                errates_spanbert[words[i]]['errs'] += err
            else:
                errates_spanbert[words[i]] = {}
                errates_spanbert[words[i]]['count'] = 1
                errates_spanbert[words[i]]['errs'] = err



In [191]:
for k, v in errates_spanbert.items():
    errates_spanbert[k]['errrate'] = errates_spanbert[k]['errs']/errates_spanbert[k]['count'] 
    if errates_spanbert[k]['errrate'] > 0 and errates_spanbert[k]['errs'] > 100:
        print(k, errates_spanbert[k]['errs'])


$ 113
said 467
new 176
died 202
group 151
-lrb- 275
-rrb- 274
president 140
first 131


In [173]:
for index, row in df_errors_spanbert.iterrows():
    if row['relation'] != row['prediction_spanbert'] and 'said' in row['example'].split(' '):
        print(row['example'])
        print("PREDICTION: ", row['prediction_spanbert'], ". RELATION: ", row['relation'])
        print(row['subj'], row['obj'])
        print()

`` she made a devastating run around the turn , '' u.s. hall of fame trainer bobby frankel said .
PREDICTION:  per:employee_of . RELATION:  no_relation
['bobby', 'frankel'] ['u.s.', 'hall', 'of', 'fame']

siemon wezeman of the stockholm international peace research institute said issues of `` national prestige '' have always blocked efforts to resolve the dispute and warned that further militarisation carried obvious dangers .
PREDICTION:  org:top_members/employees . RELATION:  no_relation
['stockholm', 'international', 'peace', 'research', 'institute'] ['siemon', 'wezeman']

finnish shipyard stx finland said tuesday it will lay off up to 400 workers at the turku shipyard where it last month completed the construction of the world 's biggest cruise liner .
PREDICTION:  org:city_of_headquarters . RELATION:  no_relation
['stx', 'finland'] ['turku']

london 2010-02-03 10:30:10 utc stockholm international peace research institute : http://wwwsipriorg/ ------ the overall amount of money inv

['stuart', 'rose'] ['retailer']

bolland , 50 , credited with reviving the fortunes of british supermarket chain morrisons since his appointment there as chief executive in 2006 , will replace briton stuart rose at the start of 2010 , m&s said in a statement .
PREDICTION:  per:employee_of . RELATION:  no_relation
['stuart', 'rose'] ['m&s']

the chairman of revenue and customs , paul gray , who only took up the role eight months ago after his predecessor quit over multi - million-pound fraud and error in the tax credits system , resigned tuesday , darling said .
PREDICTION:  per:employee_of . RELATION:  no_relation
['paul', 'gray'] ['customs']

penner , who is married to another los angeles times writer , said he started coming out about two months ago by telling his boss , his barber and a soccer teammate , and that he now feels happier and healthier .
PREDICTION:  per:title . RELATION:  no_relation
['he'] ['writer']

the body of poland 's first lady maria kaczynska remains unidentifie

PREDICTION:  no_relation . RELATION:  org:shareholders
['access', 'industries'] ['len', 'blavatnik']

`` it 's difficult to maintain growth as the outside environment was not good , '' said li rongrong , director of the state-owned assets supervision and administration commission -lrb- sasac -rrb- under the state council , adding the situation next year would be `` grim '' .
PREDICTION:  no_relation . RELATION:  org:parents
['state-owned', 'assets', 'supervision', 'and', 'administration', 'commission'] ['state', 'council']

`` the nigeria police force hereby warns that both the employers of the thugs and the thugs themselves will face the full wrath of the law as nigeria 's democracy has no more room for mischief makers , '' the statement said .
PREDICTION:  no_relation . RELATION:  org:country_of_headquarters
['nigeria', 'police', 'force'] ['nigeria']

officers were called to pekar 's suburban home by his wife about 1 a.m. , cleveland heights police capt. michael cannon said .
PREDICT

urgent : white house says obama to attend funeral of polish president washington , april 13 -lrb- xinhua -rrb- us president barack obama will travel to poland to attend the state funeral of president lech kaczynski and first lady maria kaczynska on sunday , white house said on tuesday .
PREDICTION:  per:countries_of_residence . RELATION:  per:origin
['maria', 'kaczynska'] ['poland']

mexico city , nov 23 , 2009 -lrb- afp -rrb- alvaro said his father , who now directs the washington national opera and the los angeles opera in the united states , will perform songs from spanish zarzuela , christmas songs and traditional mexican folk tunes .
PREDICTION:  no_relation . RELATION:  org:country_of_headquarters
['washington', 'national', 'opera'] ['united', 'states']

`` drug-related violence in mexico has increased , and even spilled over to areas in the country previously thought to be immune , '' said stefan hofer , an emerging - markets equity strategist at bank julius baer in zurich , whi

hours before zapata 's death , the banned cuban committee for human rights and national reconciliation -lrb- ccdhrn -rrb- had said his condition was `` very serious . ''
PREDICTION:  per:origin . RELATION:  no_relation
['zapata'] ['cuban']

stepping onto a new york sidewalk for the first time , he looked at the skyline and , as he often recalled , said , `` this is home . ''
PREDICTION:  per:stateorprovinces_of_residence . RELATION:  no_relation
['he'] ['new', 'york']

the body of poland 's first lady maria kaczynska remains unidentified more than a day after she died in an air crash with president lech kaczynski and other state officials , an aide said sunday .
PREDICTION:  per:title . RELATION:  no_relation
['maria', 'kaczynska'] ['lady']

in cairo , sheik mohammed sayed tantawi of al-azhar mosque , sunni islam 's pre-eminent institution , said it was a sin to prevent pilgrims from reaching their destination .
PREDICTION:  no_relation . RELATION:  per:cities_of_residence
['mohammed',

the american ambassador to iraq , zalmay khalilzad , said he was `` sorry '' for the detention .
PREDICTION:  no_relation . RELATION:  per:origin
['he'] ['american']

quelle deutschland , the german mail-order business of troubled department store owner arcandor ag , is to be shut down after attempts to sell it failed , arcandor 's bankruptcy administrator said .
PREDICTION:  no_relation . RELATION:  org:subsidiaries
['arcandor'] ['quelle', 'deutschland']

palestinian leader abu daoud , who planned the daring deadly attack against israeli athletes at the 1972 munich olympic games , died saturday of illness at the age of 73 , palestinian officials said .
PREDICTION:  no_relation . RELATION:  per:origin
['abu', 'daoud'] ['palestinian']

`` it is a catastrophe that policy makers have chosen to ignore way too long , '' said cecilia martinsen , a member of the stockholm international water institute .
PREDICTION:  org:top_members/employees . RELATION:  no_relation
['stockholm', 'internation

pakistan boxing federation spokesman obaid awan said chowdhry died of a heart attack in the southern port city of karachi .
PREDICTION:  per:city_of_death . RELATION:  no_relation
['chowdhry'] ['southern', 'port', 'city']

nuclear energy institute spokesman mitch singer welcomed the results of the poll and said americans clearly support increased development of nuclear energy in the united states .
PREDICTION:  org:top_members/employees . RELATION:  no_relation
['nuclear', 'energy', 'institute'] ['mitch', 'singer']

arcandor , whose businesses include germany 's karstadt department store chain and travel operator thomas cook , said last month that it was seeking government loan guarantees of around euro650 million -lrb- $ 925 million -rrb- .
PREDICTION:  no_relation . RELATION:  org:subsidiaries
['arcandor'] ['karstadt']

finance director douglas flint will take over as chairman from stephen green , who announced this month he was leaving to become britain 's trade minister at the star